## Kitchen training - test

In [1]:
import gdown
from sklearn.model_selection import train_test_split
import os
import shutil
import re
import pandas as pd

OD_PATH = '/models/research/object_detection/'
MAIN_PATH = '/happy-walrus/models/version_2/'
IMG_PATH = MAIN_PATH + 'images/'

### Resources

- [Tensorflow Object Detection API](https://github.com/tensorflow/models/tree/master/research/object_detection)
- [Tensorflow Object Detection API tutorial](https://github.com/EdjeElectronics/TensorFlow-Object-Detection-API-Tutorial-Train-Multiple-Objects-Windows-10)

# 1. Training

### Download data

Store all images and annotations in a single folder, zip the folder and store it in Google Drive under `safety/data/images/version_X` (replace the `X`).

In [2]:
# Download images
file_id = "1gnv7-2znYDCZ0Clf47A5KrqhUigBl3Ei"
file_name = "version_2.zip"
gdown.download(url="https://drive.google.com/uc?id=" + file_id,
               output=MAIN_PATH + file_name,
               quiet=False)

# Unzip images
os.mkdir(IMG_PATH)
!unzip -q {MAIN_PATH}{file_name} -d {IMG_PATH}
files_unzipped = os.listdir(MAIN_PATH + 'images/')
print('Files unzipped:', len(files_unzipped))
print('XML files:', len([file for file in files_unzipped if re.match('.*\.xml', file)]))
print('JPG files:', len([file for file in files_unzipped if re.match('.*\.jpg', file)]))

Downloading...
From: https://drive.google.com/uc?id=1gnv7-2znYDCZ0Clf47A5KrqhUigBl3Ei
To: /happy-walrus/models/version_2/version_2.zip
577MB [00:11, 52.3MB/s] 


Files unzipped: 5444
XML files: 2632
JPG files: 2811


Randomly split data into train and test:
```
|-images
    |- train
    |- test
```
where the last level folders will contain both the images and annotations (.xml) files.

In [3]:
# Create train and test folders in images/
os.mkdir(IMG_PATH + 'train')
os.mkdir(IMG_PATH + 'test')

# Get list of all files that have annotations and split into train and test
jpg_files = [file[:-4] for file in os.listdir(IMG_PATH) if re.search('.*\.jpg$', file)]
files = [file[:-4] for file in os.listdir(IMG_PATH) if re.search('.*\.xml$', file) and file[:-4] in jpg_files]
files = [file for file in files if not re.search('open_oven', file)]
files_train, files_test = train_test_split(files, train_size=0.9, test_size=0.1, random_state=2014)

# Move images to train or test folders
errors = []
for file in files_train:
    try:
        shutil.move(IMG_PATH + file + '.xml', IMG_PATH + 'train/' + file + '.xml')
        shutil.move(IMG_PATH + file + '.jpg', IMG_PATH + 'train/' + file + '.jpg')
    except Exception as err:
        errors.append([file, err])

for file in files_test:
    try:
        shutil.move(IMG_PATH + file + '.xml', IMG_PATH + 'test/' + file + '.xml')
        shutil.move(IMG_PATH + file + '.jpg', IMG_PATH + 'test/' + file + '.jpg')
    except Exception as err:
        errors.append([file, err])

# Remove remaining images
files_rm = [file for file in os.listdir(IMG_PATH) if re.search('.*\.jpg|.*\.xml', file)]
for file in files_rm:
    os.remove(IMG_PATH + file)
        
# Print errors
print("Removed files:", len(files_rm))
print("Number of errors:", len(errors))
print(errors)

Removed files: 251
Number of errors: 0
[]


### Generate data

Generate training and test data to `./images/`

In [19]:
# Generate training and test data
!python {OD_PATH}xml_to_csv.py
print("")
!head {IMG_PATH}/train_labels.csv -n 5

# Print results
print("")
train_csv =  pd.read_csv(IMG_PATH + 'train_labels.csv')
unique_classes = sorted(train_csv['class'].unique())
print("Unique classes:", unique_classes)
print("Train images:", train_csv['filename'].unique().shape[0])
print("")
print("Annotations per class:")
print(train_csv['class'].value_counts())
print("")
print("Test images:", train_csv['filename'].unique().shape[0])
print("")

# Generate label-id mapping
class_mapping = []
for count, item in enumerate(unique_classes):
    class_mapping.append('item{')
    class_mapping.append('\tid: ' + str(count + 1))
    class_mapping.append('\tname: \'' + item + '\'')
    class_mapping.append('}')
with open(MAIN_PATH + 'training/labelmap.pbtxt', 'w') as f:
    f.write('\n'.join(class_mapping))
print("Label id mapping:")
print('\n'.join(class_mapping))

Successfully converted xml to csv.
Successfully converted xml to csv.

filename,width,height,class,xmin,ymin,xmax,ymax
orange_kitchen.EH.033.jpg,1000,1000,stove,676,452,874,660
orange_kitchen.EH.033.jpg,1000,1000,chair,538,604,800,981
orange_kitchen.EH.033.jpg,1000,1000,chair,255,533,482,882
orange_kitchen.EH.033.jpg,1000,1000,chair,385,504,555,772

Unique classes: ['chair', 'ladder', 'oven', 'sofa', 'stool', 'stove']
Train images: 2192

Annotations per class:
chair     2705
stove     1950
oven       944
stool      665
sofa       103
ladder       5
Name: class, dtype: int64

Test images: 2192

Label id mapping:
item{
	id: 1
	name: 'chair'
}
item{
	id: 2
	name: 'ladder'
}
item{
	id: 3
	name: 'oven'
}
item{
	id: 4
	name: 'sofa'
}
item{
	id: 5
	name: 'stool'
}
item{
	id: 6
	name: 'stove'
}


In [10]:
!head generate_tfrecord.py -n 45 | tail -n 16

# TO-DO replace this with label map
def class_text_to_int(row_label):
    if row_label == 'chair':
        return 1
    elif row_label == 'ladder':
        return 2
    elif row_label == 'oven':
        return 3
    elif row_label == 'sofa':
        return 4
    elif row_label == 'stool':
        return 5
    elif row_label == 'stove':
        return 6
    else:
        None


Open `generate_tfrecord.py` and:
1. replace `import tensorflow` with `import tensorflow.compat.v1`.
2. Modify `class_test_to_int()` function with label-id mapping.

In [11]:
# Generate TF formatted data
!python generate_tfrecord.py --csv_input={IMG_PATH}train_labels.csv --image_dir={IMG_PATH}train --output_path=train.record
!python generate_tfrecord.py --csv_input={IMG_PATH}test_labels.csv --image_dir={IMG_PATH}test --output_path=test.record
print("")
!ls -lh | grep .*\.record$

/root/.local/lib/python3.6/site-packages/PIL/TiffImagePlugin.py:802: UserWarning: Corrupt EXIF data.  Expecting to read 12 bytes but only got 10. 
  warnings.warn(str(msg))
Successfully created the TFRecords: /happy-walrus/models/version_2/train.record
Successfully created the TFRecords: /happy-walrus/models/version_2/test.record

-rw-r--r-- 1 root root  34M Nov 14 20:32 test.record
-rw-r--r-- 1 root root 446M Nov 14 20:32 train.record


### Training

Get model checkpoint (other models in Tensorflow object detection's [Model Zoo](https://github.com/tensorflow/models/blob/master/research/object_detection/g3doc/detection_model_zoo.md)).

In [14]:
!wget "http://download.tensorflow.org/models/object_detection/faster_rcnn_inception_v2_coco_2018_01_28.tar.gz"
!tar xvzf faster_rcnn_inception_v2_coco_2018_01_28.tar.gz

--2019-11-14 20:36:19--  http://download.tensorflow.org/models/object_detection/faster_rcnn_inception_v2_coco_2018_01_28.tar.gz
Resolving download.tensorflow.org (download.tensorflow.org)... 172.217.9.16, 2607:f8b0:4000:812::2010
Connecting to download.tensorflow.org (download.tensorflow.org)|172.217.9.16|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 149119618 (142M) [application/x-tar]
Saving to: ‘faster_rcnn_inception_v2_coco_2018_01_28.tar.gz’

faster_rcnn_incepti 100%[===================>] 142.21M  72.2MB/s    in 2.0s    

2019-11-14 20:36:26 (72.2 MB/s) - ‘faster_rcnn_inception_v2_coco_2018_01_28.tar.gz’ saved [149119618/149119618]

faster_rcnn_inception_v2_coco_2018_01_28/
faster_rcnn_inception_v2_coco_2018_01_28/model.ckpt.index
faster_rcnn_inception_v2_coco_2018_01_28/checkpoint
faster_rcnn_inception_v2_coco_2018_01_28/pipeline.config
faster_rcnn_inception_v2_coco_2018_01_28/model.ckpt.data-00000-of-00001
faster_rcnn_inception_v2_coco_2018_01_28/model

1. Copy config file from `./samples/configs/` to `./training/`
2. Adapt parameters in config file:
    - `num_classes`
    - `fine_tune_checkpoint`
    - train_input_reader: `input_path`, `label_map_path`
    - `num_examples`: images/test/
    - eval_input_reader: `input_path`, `label_map_path`
    - `data_augmentation_options`, see augmentations and arguments in [preprocessor module](https://github.com/tensorflow/models/blob/master/research/object_detection/protos/preprocessor.proto).

In [72]:
# WARNING: this overwrites existing config file (copy only if no config already created)
!cp {OD_PATH}samples/configs/faster_rcnn_inception_v2_pets.config {MAIN_PATH}training/faster_rcnn_inception_v2_kitchens.config

Move train.py from `legacy/` to `.`

In [12]:
!cp {OD_PATH}legacy/train.py .

Train model
- Make sure to delete all files in trainin/ except labelmap.pbtxt and the config file.
- needs to be stopped manually)

In [16]:
!python train.py --logtostderr --train_dir={MAIN_PATH}training/ --pipeline_config_path={MAIN_PATH}training/faster_rcnn_inception_v2_kitchens.config

The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.






Instructions for updating:
Use object_detection/model_main.py.
W1114 20:38:52.744255 139700598785856 deprecation.py:323] From /usr/local/lib/python3.6/dist-packages/absl/app.py:250: main (from __main__) is deprecated and will be removed in a future version.
Instructions for updating:
Use object_detection/model_main.py.

W1114 20:38:52.744544 139700598785856 module_wrapper.py:139] From train.py:91: The name tf.gfile.MakeDirs is deprecated. Please use tf.io.gfile.makedirs instead.


W1114 20:38:52.744951 139700598785856 module_wrapper.py:139] From /models/research/object_detection/utils/config_util.py:102: The name tf.gfile.G

Instructions for updating:
Queue-based input pipelines have been replaced by `tf.data`. Use `tf.data.Dataset.batch(batch_size)` (or `padded_batch(...)` if `dynamic_pad=True`).
W1114 20:38:53.797909 139700598785856 deprecation.py:323] From /models/research/object_detection/core/batcher.py:101: batch (from tensorflow.python.training.input) is deprecated and will be removed in a future version.
Instructions for updating:
Queue-based input pipelines have been replaced by `tf.data`. Use `tf.data.Dataset.batch(batch_size)` (or `padded_batch(...)` if `dynamic_pad=True`).
Instructions for updating:
To construct input pipelines, use the `tf.data` module.
W1114 20:38:53.803235 139700598785856 deprecation.py:323] From /usr/local/lib/python3.6/dist-packages/tensorflow_core/python/training/input.py:752: QueueRunner.__init__ (from tensorflow.python.training.queue_runner_impl) is deprecated and will be removed in a future version.
Instructions for updating:
To construct input pipelines, use the `tf.d

Instructions for updating:
Use keras.layers.flatten instead.
W1114 20:38:58.284678 139700598785856 deprecation.py:323] From /usr/local/lib/python3.6/dist-packages/tensorflow_core/contrib/layers/python/layers/layers.py:1634: flatten (from tensorflow.python.layers.core) is deprecated and will be removed in a future version.
Instructions for updating:
Use keras.layers.flatten instead.
INFO:tensorflow:Scale of 0 disables regularizer.
I1114 20:38:58.288056 139700598785856 regularizers.py:98] Scale of 0 disables regularizer.
INFO:tensorflow:Scale of 0 disables regularizer.
I1114 20:38:58.312787 139700598785856 regularizers.py:98] Scale of 0 disables regularizer.

W1114 20:38:58.678637 139700598785856 module_wrapper.py:139] From /models/research/object_detection/core/losses.py:177: The name tf.losses.huber_loss is deprecated. Please use tf.compat.v1.losses.huber_loss instead.


W1114 20:38:58.680426 139700598785856 module_wrapper.py:139] From /models/research/object_detection/core/losses.py:1

Instructions for updating:
Please switch to tf.train.MonitoredTrainingSession
W1114 20:39:07.720390 139700598785856 deprecation.py:323] From /usr/local/lib/python3.6/dist-packages/tensorflow_core/contrib/slim/python/slim/learning.py:742: Supervisor.__init__ (from tensorflow.python.training.supervisor) is deprecated and will be removed in a future version.
Instructions for updating:
Please switch to tf.train.MonitoredTrainingSession
2019-11-14 20:39:08.893428: I tensorflow/core/platform/cpu_feature_guard.cc:142] Your CPU supports instructions that this TensorFlow binary was not compiled to use: AVX2 FMA
2019-11-14 20:39:08.906578: I tensorflow/core/platform/profile_utils/cpu_utils.cc:94] CPU Frequency: 2100050000 Hz
2019-11-14 20:39:08.910077: I tensorflow/compiler/xla/service/service.cc:168] XLA service 0xed35fd0 initialized for platform Host (this does not guarantee that XLA will be used). Devices:
2019-11-14 20:39:08.910157: I tensorflow/compiler/xla/service/service.cc:176]   StreamE

INFO:tensorflow:global step 33: loss = 2.0165 (1.157 sec/step)
I1114 20:40:12.323887 139700598785856 learning.py:507] global step 33: loss = 2.0165 (1.157 sec/step)
INFO:tensorflow:global step 34: loss = 2.6619 (1.235 sec/step)
I1114 20:40:13.560636 139700598785856 learning.py:507] global step 34: loss = 2.6619 (1.235 sec/step)
INFO:tensorflow:global step 35: loss = 0.5679 (1.186 sec/step)
I1114 20:40:14.747779 139700598785856 learning.py:507] global step 35: loss = 0.5679 (1.186 sec/step)
INFO:tensorflow:global step 36: loss = 2.1630 (1.255 sec/step)
I1114 20:40:16.003867 139700598785856 learning.py:507] global step 36: loss = 2.1630 (1.255 sec/step)
INFO:tensorflow:global step 37: loss = 1.8621 (1.192 sec/step)
I1114 20:40:17.196781 139700598785856 learning.py:507] global step 37: loss = 1.8621 (1.192 sec/step)
INFO:tensorflow:global step 38: loss = 2.4611 (0.891 sec/step)
I1114 20:40:18.089552 139700598785856 learning.py:507] global step 38: loss = 2.4611 (0.891 sec/step)
INFO:tenso

...

INFO:tensorflow:global step 46574: loss = 0.0619 (1.063 sec/step)
I1115 10:56:32.192744 139700598785856 learning.py:507] global step 46574: loss = 0.0619 (1.063 sec/step)
INFO:tensorflow:global step 46575: loss = 0.1090 (0.906 sec/step)
I1115 10:56:33.100567 139700598785856 learning.py:507] global step 46575: loss = 0.1090 (0.906 sec/step)
INFO:tensorflow:global step 46576: loss = 0.0957 (1.085 sec/step)
I1115 10:56:34.186656 139700598785856 learning.py:507] global step 46576: loss = 0.0957 (1.085 sec/step)
INFO:tensorflow:global step 46577: loss = 0.7624 (1.104 sec/step)
I1115 10:56:35.292043 139700598785856 learning.py:507] global step 46577: loss = 0.7624 (1.104 sec/step)
INFO:tensorflow:global step 46578: loss = 0.2210 (1.081 sec/step)
I1115 10:56:36.374003 139700598785856 learning.py:507] global step 46578: loss = 0.2210 (1.081 sec/step)
INFO:tensorflow:global step 46579: loss = 0.2974 (1.193 sec/step)
I1115 10:56:37.567771 139700598785856 learning.py:507] global step 46579: loss 

INFO:tensorflow:global step 46622: loss = 0.3206 (1.344 sec/step)
I1115 10:57:25.753865 139700598785856 learning.py:507] global step 46622: loss = 0.3206 (1.344 sec/step)
INFO:tensorflow:global step 46623: loss = 0.0392 (1.057 sec/step)
I1115 10:57:26.812586 139700598785856 learning.py:507] global step 46623: loss = 0.0392 (1.057 sec/step)
INFO:tensorflow:global step 46624: loss = 0.4653 (1.127 sec/step)
I1115 10:57:27.940621 139700598785856 learning.py:507] global step 46624: loss = 0.4653 (1.127 sec/step)
INFO:tensorflow:global step 46625: loss = 0.0600 (0.808 sec/step)
I1115 10:57:28.749684 139700598785856 learning.py:507] global step 46625: loss = 0.0600 (0.808 sec/step)
INFO:tensorflow:global step 46626: loss = 0.0671 (1.204 sec/step)
I1115 10:57:29.955261 139700598785856 learning.py:507] global step 46626: loss = 0.0671 (1.204 sec/step)
INFO:tensorflow:global step 46627: loss = 0.0952 (1.137 sec/step)
I1115 10:57:31.093925 139700598785856 learning.py:507] global step 46627: loss 

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



INFO:tensorflow:global step 47902: loss = 0.0248 (1.171 sec/step)
I1115 11:21:17.024294 139700598785856 learning.py:507] global step 47902: loss = 0.0248 (1.171 sec/step)
INFO:tensorflow:global step 47903: loss = 0.0185 (1.221 sec/step)
I1115 11:21:18.247099 139700598785856 learning.py:507] global step 47903: loss = 0.0185 (1.221 sec/step)
INFO:tensorflow:global step 47904: loss = 0.1408 (1.345 sec/step)
I1115 11:21:19.593428 139700598785856 learning.py:507] global step 47904: loss = 0.1408 (1.345 sec/step)
INFO:tensorflow:global step 47905: loss = 0.1063 (1.275 sec/step)
I1115 11:21:20.869987 139700598785856 learning.py:507] global step 47905: loss = 0.1063 (1.275 sec/step)
INFO:tensorflow:Recording summary at step 47905.
I1115 11:21:21.920037 139688752957184 supervisor.py:1050] Recording summary at step 47905.
INFO:tensorflow:global step 47906: loss = 0.0545 (1.112 sec/step)
I1115 11:21:21.983756 139700598785856 learning.py:507] global step 47906: loss = 0.0545 (1.112 sec/step)
INFO:

INFO:tensorflow:global step 47950: loss = 0.1383 (1.083 sec/step)
I1115 11:22:09.880977 139700598785856 learning.py:507] global step 47950: loss = 0.1383 (1.083 sec/step)
INFO:tensorflow:global step 47951: loss = 0.1131 (1.251 sec/step)
I1115 11:22:11.133353 139700598785856 learning.py:507] global step 47951: loss = 0.1131 (1.251 sec/step)
INFO:tensorflow:global step 47952: loss = 0.0354 (1.245 sec/step)
I1115 11:22:12.379667 139700598785856 learning.py:507] global step 47952: loss = 0.0354 (1.245 sec/step)
INFO:tensorflow:global step 47953: loss = 0.1009 (1.210 sec/step)
I1115 11:22:13.591427 139700598785856 learning.py:507] global step 47953: loss = 0.1009 (1.210 sec/step)
INFO:tensorflow:global step 47954: loss = 0.0592 (0.787 sec/step)
I1115 11:22:14.379615 139700598785856 learning.py:507] global step 47954: loss = 0.0592 (0.787 sec/step)
INFO:tensorflow:global step 47955: loss = 0.0811 (0.813 sec/step)
I1115 11:22:15.194092 139700598785856 learning.py:507] global step 47955: loss 

In command line, run `tensorboard --logdir=/happy-walrus/models/version_2/training`

### Export model

In [17]:
!ls -l training/

total 768236
-rw-r--r-- 1 root root       517 Nov 15 11:19 checkpoint
-rw-r--r-- 1 root root 232937451 Nov 15 11:21 events.out.tfevents.1573763961.d93712a46288
-rw-r--r-- 1 root root      4427 Nov 13 21:41 faster_rcnn_inception_v2_kitchens.config
-rw-r--r-- 1 root root  10469360 Nov 14 20:39 graph.pbtxt
-rw-r--r-- 1 root root       178 Nov 14 20:26 labelmap.pbtxt
-rw-r--r-- 1 root root       202 Nov 13 21:41 labelmap.pbtxt.bak
-rw-r--r-- 1 root root 103173376 Nov 15 10:39 model.ckpt-45643.data-00000-of-00001
-rw-r--r-- 1 root root     25563 Nov 15 10:39 model.ckpt-45643.index
-rw-r--r-- 1 root root   5441061 Nov 15 10:39 model.ckpt-45643.meta
-rw-r--r-- 1 root root 103173376 Nov 15 10:49 model.ckpt-46185.data-00000-of-00001
-rw-r--r-- 1 root root     25563 Nov 15 10:49 model.ckpt-46185.index
-rw-r--r-- 1 root root   5441061 Nov 15 10:49 model.ckpt-46185.meta
-rw-r--r-- 1 root root 103173376 Nov 15 10:59 model.ckpt-46725.data-00000-of-00001
-rw-r--r-- 1 root root     25563 Nov 15 10:59 

In [16]:
%%bash
ckpt_step = 1295
python {OD_PATH}export_inference_graph.py --input_type image_tensor --pipeline_config_path training/faster_rcnn_inception_v2_kitchens.config --trained_checkpoint_prefix training/model.ckpt-{ckpt_step} --output_directory inference_graph

The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.





W1104 16:28:48.156948 140301050382144 module_wrapper.py:139] From /models/research/object_detection/export_inference_graph.py:145: The name tf.gfile.GFile is deprecated. Please use tf.io.gfile.GFile instead.


W1104 16:28:48.168290 140301050382144 module_wrapper.py:139] From /models/research/object_detection/exporter.py:389: The name tf.gfile.MakeDirs is deprecated. Please use tf.io.gfile.makedirs instead.


W1104 16:28:48.169805 140301050382144 module_wrapper.py:139] From /models/research/object_detection/exporter.py:121: The name tf.placeholder is deprecated. Please use tf.compat.v1.placeholder instead.


W1104 16:28:48.25


W1104 16:28:53.766587 140301050382144 module_wrapper.py:139] From /models/research/object_detection/exporter.py:268: The name tf.add_to_collection is deprecated. Please use tf.compat.v1.add_to_collection instead.

Instructions for updating:
Please switch to tf.train.get_or_create_global_step
W1104 16:28:53.766983 140301050382144 deprecation.py:323] From /models/research/object_detection/exporter.py:370: get_or_create_global_step (from tensorflow.contrib.framework.python.ops.variables) is deprecated and will be removed in a future version.
Instructions for updating:
Please switch to tf.train.get_or_create_global_step

W1104 16:28:53.770792 140301050382144 module_wrapper.py:139] From /models/research/object_detection/exporter.py:402: The name tf.get_default_graph is deprecated. Please use tf.compat.v1.get_default_graph instead.

Instructions for updating:
Use `tf.profiler.profile(graph, run_meta, op_log, cmd, options)`. Build `options` with `tf.profiler.ProfileOptionBuilder`. See README

234 ops no flops stats due to incomplete shapes.
Parsing Inputs...
Incomplete shape.

=========================Options=============================
-max_depth                  10000
-min_bytes                  0
-min_peak_bytes             0
-min_residual_bytes         0
-min_output_bytes           0
-min_micros                 0
-min_accelerator_micros     0
-min_cpu_micros             0
-min_params                 0
-min_float_ops              1
-min_occurrence             0
-step                       -1
-order_by                   float_ops
-account_type_regexes       .*
-start_name_regexes         .*
-trim_name_regexes          .*BatchNorm.*,.*Initializer.*,.*Regularizer.*,.*BiasAdd.*
-show_name_regexes          .*
-hide_name_regexes          
-account_displayed_op_only  true
-select                     float_ops
-output                     stdout:

==================Model Analysis Report======================
Incomplete shape.

Doc:
scope: The nodes in the model graph are organiz


W1104 16:28:55.322115 140301050382144 module_wrapper.py:139] From /models/research/object_detection/exporter.py:419: The name tf.train.Saver is deprecated. Please use tf.compat.v1.train.Saver instead.


W1104 16:28:56.493039 140301050382144 module_wrapper.py:139] From /models/research/object_detection/exporter.py:332: The name tf.Session is deprecated. Please use tf.compat.v1.Session instead.

2019-11-04 16:28:56.493579: W tensorflow/stream_executor/platform/default/dso_loader.cc:55] Could not load dynamic library 'libcuda.so.1'; dlerror: libcuda.so.1: cannot open shared object file: No such file or directory
2019-11-04 16:28:56.493635: E tensorflow/stream_executor/cuda/cuda_driver.cc:318] failed call to cuInit: UNKNOWN ERROR (303)
2019-11-04 16:28:56.493702: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:156] kernel driver does not appear to be running on this host (74a0ad80ad34): /proc/driver/nvidia/version does not exist
2019-11-04 16:28:56.494113: I tensorflow/core/platform


W1104 16:29:05.716187 140301050382144 module_wrapper.py:139] From /models/research/object_detection/utils/config_util.py:188: The name tf.gfile.Open is deprecated. Please use tf.io.gfile.GFile instead.

INFO:tensorflow:Writing pipeline config file to inference_graph/pipeline.config
I1104 16:29:05.716538 140301050382144 config_util.py:190] Writing pipeline config file to inference_graph/pipeline.config


In [17]:
!ls -lh inference_graph/

total 101M
-rwxr-xr-x 1 root root   77 Nov  4 16:28 checkpoint
-rwxr-xr-x 1 root root  136 Nov  4 14:50 desktop.ini
-rwxr-xr-x 1 root root  50M Nov  4 16:29 frozen_inference_graph.pb
-rwxr-xr-x 1 root root  50M Nov  4 16:28 model.ckpt.data-00000-of-00001
-rwxr-xr-x 1 root root  16K Nov  4 16:28 model.ckpt.index
-rwxr-xr-x 1 root root 1.8M Nov  4 16:28 model.ckpt.meta
-rwxr-xr-x 1 root root 3.1K Nov  4 16:29 pipeline.config
drwxrwxrwx 2 root root    0 Nov  4 16:29 saved_model


Download model and store it in Google Drive for use in next section.

# 2. Evaluation

### Download model

Store all images and annotations in a single folder, zip the folder and store it in Google Drive under `safety/data/images/version_X` (replace the `X`).

In [2]:
# Download images
file_id = "1gnv7-2znYDCZ0Clf47A5KrqhUigBl3Ei"
file_name = "version_2.zip"
gdown.download(url="https://drive.google.com/uc?id=" + file_id,
               output=MAIN_PATH + file_name,
               quiet=False)

# Unzip images
os.mkdir(IMG_PATH)
!unzip -q {MAIN_PATH}{file_name} -d {IMG_PATH}
files_unzipped = os.listdir(MAIN_PATH + 'images/')
print('Files unzipped:', len(files_unzipped))
print('XML files:', len([file for file in files_unzipped if re.match('.*\.xml', file)]))
print('JPG files:', len([file for file in files_unzipped if re.match('.*\.jpg', file)]))

Downloading...
From: https://drive.google.com/uc?id=1gnv7-2znYDCZ0Clf47A5KrqhUigBl3Ei
To: /happy-walrus/models/version_2/version_2.zip
577MB [00:11, 52.3MB/s] 


Files unzipped: 5444
XML files: 2632
JPG files: 2811


### Perform inference

To `Object_detection_image.py`:
1. add before last line `cv2.imwrite('/path/to/save/boxed_image.JPG', image)` and comment last line out.
1. `NUM_CLASSES`
1. `IMAGE_NAME`
1. 

In [20]:
!cat Object_detection_image.py

If `NoneType` related error, reinstall opencv with `apt install opencv-python`.

In [21]:
!python Object_detection_image.py

Traceback (most recent call last):
  File "Object_detection_image.py", line 29, in <module>
    from utils import label_map_util
ModuleNotFoundError: No module named 'utils'


### Evaluation metrics

Make inferences on test images

In [ ]:
%%bashsh
mkdir {MAIN_PATH}evaluation
python -m {OD_PATH}inference/infer_detections \
  --input_tfrecord_paths={MAIN_PATH}test.record \
  --output_tfrecord_path={MAIN_PATH}evaluation/test_detections.tfrecord-00000-of-00001 \
  --inference_graph=inference_graph/frozen_inference_graph.pb \
  --discard_image_pixels

Calculate performance metrics

In [ ]:
%%bash
SPLIT=test  # or validation
NUM_SHARDS=1  # Set to NUM_GPUS if using the parallel evaluation script

echo "
label_map_path: '/happy-walrus/models/version_2/training/labelmap.pbtxt'
tf_record_input_reader: { input_path: 'test.record' }
" > ${MAIN_PATH}evaluation/${SPLIT}_input_config.pbtxt

echo "
metrics_set: 'oid_V2_detection_metrics'
" > ${MAIN_PATH}evaluation/${SPLIT}_eval_config.pbtxt

python -m /models/research/object_detection/metrics/offline_eval_map_corloc.py \
  --eval_dir=${SPLIT}_eval_metrics \
  --eval_config_path=${SPLIT}_eval_metrics/${SPLIT}_eval_config.pbtxt \
  --input_config_path=${SPLIT}_eval_metrics/${SPLIT}_input_config.pbtxt